In [2]:
# Solving the stochastic Optimal Growth model by Value Function Interation 
# adapted from Fabrice Collard's Matlab code, http://fabcol.free.fr/
# tested in Julia 0.6.1.1
# this code is part of chapter 4, "Dynamic Programming" from the book: "Introduction to Quantitative Macroeconomics with Julia"
# Academic Press - Elsevier
# for comments, email at: petre(dot)caraiani(at)gmail(dot)com

sigma   = 1.5;
delta   = 0.1;
beta    = 0.95;
alpha   = 0.30;
p       = 0.9;
PI      = [p 1-p;1-p p];
se      = 0.2;
ab      = 0;
am      = exp(ab-se);
as      = exp(ab+se);
A       = [am as];
nba     = 2;


In [3]:
ks    = ((1-beta*(1-delta))/(alpha*beta))^(1/(alpha-1));
csy   = 1-alpha*beta*delta/(1-beta*(1-delta));
dev   = 0.9;
kmin  = (1-dev)*ks;
kmax  = (1+dev)*ks;
nbk   = 1000;
devk  = (kmax-kmin)/(nbk-1);
k     = collect(linspace(kmin,kmax,nbk));
kp    = zeros(nbk, nba);
c     = zeros(nbk,nba);
u     = zeros(nbk,nba);
v     = zeros(nbk,nba);
Tv    = zeros(nbk,nba);
iter  = 1;
crit  = 1;
tol   = 1e-6;
dr    = zeros(nbk,nba);             # decision rule (will contain indices)

In [4]:
#iterate on Value Function
while crit>tol
for i=1:nbk
    for j=1:nba
         c        = A[j]*k[i]^alpha+(1-delta)*k[i]-k;
         neg      = find(x -> x <=0.0,c);     
         c[neg]   = NaN;
         u[:,j]   = (c.^(1-sigma)-1)/(1-sigma);
         u[neg,j] = -1e12;  
    end;
        (Tv[i,:],dr[i,:]) = findmax(u+beta*(v*PI),1);
        dr[i,2]=dr[i,2]-nbk;
end;
   
   error = abs.(Tv-v);
   crit  = maximum((error));
   v     = copy(Tv);
   iter  = iter+1;
    end;

In [5]:
#solution
for i=1:nbk 
   for j=1:nba 
   
   index=trunc(Int, dr[i,j]);
   kp[i,j]= k[index];
        
   end;       
    end;

1000×2 Array{Float64,2}:
 0.404507  0.546439
 0.409238  0.55117 
 0.413969  0.555901
 0.4187    0.565363
 0.423431  0.570094
 0.428162  0.574825
 0.432893  0.579556
 0.437624  0.584288
 0.442355  0.59375 
 0.447086  0.598481
 0.451817  0.603212
 0.456549  0.607943
 0.46128   0.612674
 ⋮                 
 4.43065   4.86591 
 4.43538   4.87064 
 4.43538   4.87064 
 4.44011   4.87537 
 4.44484   4.8801  
 4.44957   4.88483 
 4.45431   4.88956 
 4.45904   4.8943  
 4.45904   4.89903 
 4.46377   4.89903 
 4.4685    4.90376 
 4.47323   4.90849 

In [6]:
#solution
c     = zeros(nbk,nba);
for j=1:nba;
   c[:,j] = A[j]*k.^alpha+(1-delta)*k-kp[:,j];
end
u    = (c.^(1-sigma)-1)/(1-sigma);
v    = u/(1-beta);

1000×2 Array{Float64,2}:
 -24.8901   -16.1404 
 -24.6801   -15.9249 
 -24.4751   -15.7148 
 -24.275    -15.7645 
 -24.0796   -15.5618 
 -23.8887   -15.3638 
 -23.702    -15.1705 
 -23.5195   -14.9816 
 -23.341    -15.0419 
 -23.1663   -14.859  
 -22.9953   -14.6801 
 -22.8279   -14.5051 
 -22.6639   -14.3338 
   ⋮                 
   5.37245    7.86316
   5.37124    7.86414
   5.43127    7.91405
   5.43006    7.91501
   5.42884    7.91597
   5.42763    7.91692
   5.42641    7.91786
   5.42518    7.91881
   5.48491    7.91974
   5.48368    7.96937
   5.48246    7.9703 
   5.48123    7.97122

In [7]:
#Pkg.add("Plots")
using Plots
plotly() # Choose the Plotly.jl backend for web interactivity
#plot(k',c',linewidth=1,label="Consumption",title="Consumption vs capital stock")
plot(k,c, linewidth=1,title="Consumption vs Capital Stock", label="Consumption")
